In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns

# Load the data
data = pd.read_csv(r"C:/Users/19257/Downloads/taiwanese+bankruptcy+prediction/data.csv")

# Step 1: Inspect the Data
print(data.info())
print(data.describe())

# Step 2: Data Cleaning
# Check for missing values
missing_values = data.isnull().sum()
print("Missing values:\n", missing_values[missing_values > 0])

# Step 3: Univariate Analysis
# Summary statistics
print(data.describe())

"""
# Distribution plots
for column in data.select_dtypes(include=np.number).columns:
    plt.figure(figsize=(10, 6))
    sns.histplot(data[column], kde=True)
    plt.title(f'Distribution of {column}')
    plt.show()
"""

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 6819 entries, 0 to 6818
Data columns (total 96 columns):
 #   Column                                                    Non-Null Count  Dtype  
---  ------                                                    --------------  -----  
 0   Bankrupt?                                                 6819 non-null   int64  
 1    ROA(C) before interest and depreciation before interest  6819 non-null   float64
 2    ROA(A) before interest and % after tax                   6819 non-null   float64
 3    ROA(B) before interest and depreciation after tax        6819 non-null   float64
 4    Operating Gross Margin                                   6819 non-null   float64
 5    Realized Sales Gross Margin                              6819 non-null   float64
 6    Operating Profit Rate                                    6819 non-null   float64
 7    Pre-tax net Interest Rate                                6819 non-null   float64
 8    After-tax net Int

"\n# Distribution plots\nfor column in data.select_dtypes(include=np.number).columns:\n    plt.figure(figsize=(10, 6))\n    sns.histplot(data[column], kde=True)\n    plt.title(f'Distribution of {column}')\n    plt.show()\n"

In [10]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns


In [3]:
# Step 4: Bivariate Analysis
# Correlation matrix
plt.figure(figsize=(120, 96))
corr_matrix = data.corr()
sns.heatmap(corr_matrix, annot=True, fmt=".2f")
plt.title('Correlation Matrix')
plt.show()


In [5]:
# Calculate the correlation matrix
correlation_matrix = data.corr()

# Identify highly correlated pairs (threshold = 0.9)
threshold = 0.9
highly_correlated_pairs = []

for i in range(len(correlation_matrix.columns)):
    for j in range(i):
        if abs(correlation_matrix.iloc[i, j]) > threshold:
            highly_correlated_pairs.append((correlation_matrix.columns[i], correlation_matrix.columns[j], correlation_matrix.iloc[i, j]))

# Create a DataFrame for highly correlated pairs
correlated_pairs_df = pd.DataFrame(highly_correlated_pairs, columns=['Variable 1', 'Variable 2', 'Correlation Score'])

# Display the correlated pairs
print(correlated_pairs_df)

# Save the DataFrame to a CSV file
correlated_pairs_df.to_csv('highly_correlated_pairs.csv', index=False)


                                           Variable 1  \
0              ROA(A) before interest and % after tax   
1    ROA(B) before interest and depreciation after...   
2    ROA(B) before interest and depreciation after...   
3                         Realized Sales Gross Margin   
4                           Pre-tax net Interest Rate   
5                         After-tax net Interest Rate   
6                Continuous interest rate (after tax)   
7                Continuous interest rate (after tax)   
8                Continuous interest rate (after tax)   
9                             Net Value Per Share (A)   
10                            Net Value Per Share (C)   
11                            Net Value Per Share (C)   
12           Per Share Net profit before tax (Yuan ¥)   
13                     Regular Net Profit Growth Rate   
14                                   Net worth/Assets   
15                   Operating profit/Paid-in capital   
16              Net profit befo

In [8]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
from sklearn.preprocessing import StandardScaler
from sklearn.decomposition import PCA
from sklearn.model_selection import train_test_split, cross_val_score, GridSearchCV
from sklearn.ensemble import RandomForestClassifier, GradientBoostingClassifier
from sklearn.linear_model import LogisticRegression
from sklearn.svm import SVC
from sklearn.metrics import classification_report, accuracy_score, f1_score
from imblearn.over_sampling import SMOTE

# Load the data
data = pd.read_csv('path_to_your_file.csv')

# Step 1: Inspect the Data
print(data.info())
print(data.describe())

# Step 2: Data Cleaning
# Check for missing values
missing_values = data.isnull().sum()
print("Missing values:\n", missing_values[missing_values > 0])

# Step 3: Remove Highly Correlated Features
correlation_matrix = data.corr()
threshold = 0.9
columns_to_remove = set()

for i in range(len(correlation_matrix.columns)):
    for j in range(i):
        if abs(correlation_matrix.iloc[i, j]) > threshold:
            columns_to_remove.add(correlation_matrix.columns[i])

data_reduced = data.drop(columns=columns_to_remove)

# Step 4: Target Variable Analysis
# Class distribution
print(data_reduced['Bankrupt?'].value_counts())

# Step 5: Feature Engineering
X = data_reduced.drop(columns=['Bankrupt?'])
y = data_reduced['Bankrupt?']

# Apply SMOTE to balance the dataset
smote = SMOTE(random_state=42)
X_resampled, y_resampled = smote.fit_resample(X, y)

# Feature scaling
scaler = StandardScaler()
X_scaled = scaler.fit_transform(X_resampled)

# Apply PCA
pca = PCA(n_components=0.95)  # Retain 95% of the variance
X_pca = pca.fit_transform(X_scaled)

# Split the data
X_train, X_test, y_train, y_test = train_test_split(X_pca, y_resampled, test_size=0.2, random_state=42)

# Step 6: Model Training and Evaluation
models = {
    'Logistic Regression': LogisticRegression(random_state=42),
    'Random Forest': RandomForestClassifier(random_state=42),
    'Gradient Boosting': GradientBoostingClassifier(random_state=42),
    'SVM': SVC(random_state=42)
}

best_model = None
best_score = 0

for name, model in models.items():
    model.fit(X_train, y_train)
    y_pred = model.predict(X_test)
    score = f1_score(y_test, y_pred)
    print(f"{name} F1 Score: {score:.4f}")
    if score > best_score:
        best_score = score
        best_model = model

print(f"Best Model: {best_model}")

# Step 7: Hyperparameter Tuning for the Best Model
param_grid = {
    'Random Forest': {
        'n_estimators': [100, 200, 300],
        'max_depth': [None, 10, 20, 30],
        'min_samples_split': [2, 5, 10]
    },
    'Gradient Boosting': {
        'n_estimators': [100, 200, 300],
        'learning_rate': [0.01, 0.1, 0.2],
        'max_depth': [3, 5, 7]
    },
    'SVM': {
        'C': [0.1, 1, 10],
        'kernel': ['linear', 'rbf', 'poly']
    }
}

if isinstance(best_model, RandomForestClassifier):
    grid_search = GridSearchCV(best_model, param_grid['Random Forest'], cv=5, scoring='f1', n_jobs=-1)
elif isinstance(best_model, GradientBoostingClassifier):
    grid_search = GridSearchCV(best_model, param_grid['Gradient Boosting'], cv=5, scoring='f1', n_jobs=-1)
elif isinstance(best_model, SVC):
    grid_search = GridSearchCV(best_model, param_grid['SVM'], cv=5, scoring='f1', n_jobs=-1)
else:
    grid_search = None

if grid_search is not None:
    grid_search.fit(X_train, y_train)
    best_model = grid_search.best_estimator_
    print("Best parameters:", grid_search.best_params_)
    print("Best cross-validation score:", grid_search.best_score_)

# Step 8: Final Model Evaluation
y_pred = best_model.predict(X_test)
print("Final Model Evaluation:")
print(classification_report(y_test, y_pred))
print(f"Final Model Accuracy: {accuracy_score(y_test, y_pred):.4f}")
print(f"Final Model F1 Score: {f1_score(y_test, y_pred):.4f}")


FileNotFoundError: [Errno 2] No such file or directory: 'path_to_your_file.csv'

In [7]:
correlated_pairs_df.head(30)

Variable 1  \
0              ROA(A) before interest and % after tax   
1    ROA(B) before interest and depreciation after...   
2    ROA(B) before interest and depreciation after...   
3                         Realized Sales Gross Margin   
4                           Pre-tax net Interest Rate   
5                         After-tax net Interest Rate   
6                Continuous interest rate (after tax)   
7                Continuous interest rate (after tax)   
8                Continuous interest rate (after tax)   
9                             Net Value Per Share (A)   
10                            Net Value Per Share (C)   
11                            Net Value Per Share (C)   
12           Per Share Net profit before tax (Yuan ¥)   
13                     Regular Net Profit Growth Rate   
14                                   Net worth/Assets   
15                   Operating profit/Paid-in capital   
16              Net profit before tax/Paid-in capital   
17              Net profit before tax/Paid-in capital   
18                                 Cash Flow to Sales   
19                     Current Liability to Liability   
20                        Current Liability to Equity   
21                         Net Income to Total Assets   
22                         Net Income to Total Assets   
23                              Gross Profit to Sales   
24                              Gross Profit to Sales   
25                                Liability to Equity   
26                                Liability to Equity   
27                                Liability to Equity   

                                           Variable 2  Correlation Score  
0    ROA(C) before interest and depreciation befor...           0.940124  
1    ROA(C) before interest and depreciation befor...           0.986849  
2              ROA(A) before interest and % after tax           0.955741  
3                              Operating Gross Margin           0.999518  
4                               Operating Profit Rate           0.916448  
5                           Pre-tax net Interest Rate           0.986379  
6                               Operating Profit Rate           0.915544  
7                           Pre-tax net Interest Rate           0.993617  
8                         After-tax net Interest Rate           0.984452  
9                             Net Value Per Share (B)           0.999342  
10                            Net Value Per Share (B)           0.999179  
11                            Net Value Per Share (A)           0.999837  
12            Persistent EPS in the Last Four Seasons           0.955591  
13                   After-tax Net Profit Growth Rate           0.996186  
14                                       Debt ratio %          -1.000000  
15                Operating Profit Per Share (Yuan ¥)           0.998696  
16            Persistent EPS in the Last Four Seasons           0.959461  
17           Per Share Net profit before tax (Yuan ¥)           0.962723  
18                     Working capitcal Turnover Rate           0.948194  
19                      Current Liabilities/Liability           1.000000  
20                         Current Liabilities/Equity           1.000000  
21             ROA(A) before interest and % after tax           0.961552  
22   ROA(B) before interest and depreciation after...           0.912040  
23                             Operating Gross Margin           1.000000  
24                        Realized Sales Gross Margin           0.999518  
25                               Borrowing dependency           0.955857  
26                         Current Liabilities/Equity           0.963908  
27                        Current Liability to Equity           0.963908

In [ ]:

# Scatter plots
sns.pairplot(data, vars=data.columns[:5], hue='Bankrupt?')
plt.show()

# Step 5: Multivariate Analysis
# Pair plots
sns.pairplot(data, hue='Bankrupt?')
plt.show()

# Step 6: Target Variable Analysis
# Class distribution
print(data['Bankrupt?'].value_counts())

# Feature importance using a simple RandomForest model
from sklearn.ensemble import RandomForestClassifier

# Prepare the data
X = data.drop(columns=['Bankrupt?'])
y = data['Bankrupt?']

# Train a RandomForest model
model = RandomForestClassifier(n_estimators=100, random_state=42)
model.fit(X, y)

# Get feature importances
importances = model.feature_importances_
indices = np.argsort(importances)[::-1]

# Print the feature ranking
print("Feature ranking:")
for f in range(X.shape[1]):
    print(f"{f + 1}. Feature {X.columns[indices[f]]} ({importances[indices[f]]})")

# Plot the feature importances
plt.figure(figsize=(12, 8))
plt.title("Feature importances")
plt.bar(range(X.shape[1]), importances[indices], align="center")
plt.xticks(range(X.shape[1]), X.columns[indices], rotation=90)
plt.xlim([-1, X.shape[1]])
plt.show()


In [ ]:
from imblearn.over_sampling import SMOTE

# Apply SMOTE to balance the dataset
smote = SMOTE(random_state=42)
X_resampled, y_resampled = smote.fit_resample(X, y)

print("Original dataset shape:", y.value_counts())
print("Resampled dataset shape:", pd.Series(y_resampled).value_counts())


In [ ]:
from sklearn.preprocessing import StandardScaler

# Feature scaling
scaler = StandardScaler()
X_scaled = scaler.fit_transform(X_resampled)


In [ ]:
from sklearn.preprocessing import StandardScaler

# Feature scaling
scaler = StandardScaler()
X_scaled = scaler.fit_transform(X_resampled)


In [ ]:
from sklearn.model_selection import train_test_split, cross_val_score
from sklearn.ensemble import RandomForestClassifier
from sklearn.metrics import classification_report

# Split the data
X_train, X_test, y_train, y_test = train_test_split(X_pca, y_resampled, test_size=0.2, random_state=42)

# Train a RandomForest model
model = RandomForestClassifier(random_state=42)
model.fit(X_train, y_train)

# Evaluate the model
y_pred = model.predict(X_test)
print(classification_report(y_test, y_pred))

# Cross-validation
cv_scores = cross_val_score(model, X_pca, y_resampled, cv=5)
print("Cross-validation scores:", cv_scores)


In [ ]:
from sklearn.model_selection import GridSearchCV

# Hyperparameter tuning
param_grid = {
    'n_estimators': [100, 200, 300],
    'max_depth': [None, 10, 20, 30],
    'min_samples_split': [2, 5, 10]
}

grid_search = GridSearchCV(model, param_grid, cv=5, scoring='f1', n_jobs=-1)
grid_search.fit(X_train, y_train)

print("Best parameters:", grid_search.best_params_)
print("Best cross-validation score:", grid_search.best_score_)


In [ ]:
from imblearn.over_sampling import SMOTE

# Apply SMOTE to balance the dataset
smote = SMOTE(random_state=42)
X_resampled, y_resampled = smote.fit_resample(X, y)

# Check the shape of the resampled dataset
X_resampled.shape, y_resampled.shape

In [ ]:
from sklearn.preprocessing import StandardScaler

# Feature scaling
scaler = StandardScaler()
X_scaled = scaler.fit_transform(X_resampled)

In [ ]:
from sklearn.decomposition import PCA

# Apply PCA
pca = PCA(n_components=0.95)  # Retain 95% of the variance
X_pca = pca.fit_transform(X_scaled)

# Check the shape of the transformed data
X_pca.shape